In [ ]:
import numpy as np

from bokeh.layouts import row, widgetbox
from bokeh.models import CustomJS, Slider
from bokeh.plotting import figure, output_file, show, ColumnDataSource
from bokeh.io import output_notebook

x = np.linspace(0, 10, 500)
y = np.sin(x)

source = ColumnDataSource(data=dict(x=x, y=y))

plot = figure(y_range=(-10, 10), plot_width=400, plot_height=400)

plot.line('x', 'y', source=source, line_width=3, line_alpha=0.6)

callback = CustomJS(args=dict(source=source), code="""
    var data = source.data;
    var A = amp.value;
    var k = freq.value;
    var phi = phase.value;
    var B = offset.value;
    var x = data['x']
    var y = data['y']
    for (var i = 0; i < x.length; i++) {
        y[i] = B + A*Math.sin(k*x[i]+phi);
    }
    source.change.emit();
""")

amp_slider = Slider(start=0.1, end=10, value=1, step=.1,
                    title="Amplitude", callback=callback)
callback.args["amp"] = amp_slider

freq_slider = Slider(start=0.1, end=10, value=1, step=.1,
                     title="Frequency", callback=callback)
callback.args["freq"] = freq_slider

phase_slider = Slider(start=0, end=6.4, value=0, step=.1,
                      title="Phase", callback=callback)
callback.args["phase"] = phase_slider

offset_slider = Slider(start=-5, end=5, value=0, step=.1,
                       title="Offset", callback=callback)
callback.args["offset"] = offset_slider

layout = row(
    widgetbox(amp_slider, freq_slider, phase_slider, offset_slider),
    
    plot,
)

output_notebook()

show(layout)

In [ ]:
from bokeh.layouts import column
from bokeh.models import CustomJS, ColumnDataSource, Slider
from bokeh.plotting import Figure, output_file, show

x = [x*0.005 for x in range(0, 200)]
y = x

source = ColumnDataSource(data=dict(x=x, y=y))

plot = Figure(plot_width=400, plot_height=400)
plot.line('x', 'y', source=source, line_width=3, line_alpha=0.6)


callback = CustomJS(args=dict(source=source), code="""
    var data = source.data;
    
    var f = power.value;
    var x = data['x'];
    var y = data['y'];
    
    for (var i = 0; i < x.length; i++) {
        y[i] = Math.pow(x[i], f);
    }
    source.change.emit();
""")

power_slider = Slider(start=0.1, end=4, value=1, step=.1, title="Power", callback=callback)
callback.args["power"] = power_slider

layout = column(power_slider, plot)

show(layout)

In [ ]:
from bokeh.layouts import column
from bokeh.models import CustomJS, ColumnDataSource, Slider
from bokeh.plotting import Figure, output_file, show

x = [x*0.005 for x in range(0, 200)]
y = [x1 - 0.5 for x1 in x]
pt_x = [0.5]
pt_y = [pt_x[0] - 0.5]

source = ColumnDataSource(data=dict(x=x, y=y))
pt_source = ColumnDataSource(data=dict(pt_x=pt_x, pt_y=pt_y))

plot = Figure(plot_width=400, plot_height=400)
plot.line('x', 'y', source=source, line_width=3, line_alpha=0.6)

plot.circle('pt_x', 'pt_y', source=pt_source, size=20, color="navy", alpha=0.5)

callback = CustomJS(args=dict(source=source, pt_source=pt_source), code="""
    var data = source.data;
    var pt_data = pt_source.data;
    
    var f = power.value;
    var x = data['x'];
    var y = data['y'];
    
    var pt_x = pt_data['pt_x']
    var pt_y = pt_data['pt_y']
    
    pt_x[0] = pt.value;
    pt_y[0] = Math.pow(pt_x[0], f) - 0.5;
    
    for (var i = 0; i < x.length; i++) {
        y[i] = Math.pow(x[i], f) - 0.5;
    }
    source.change.emit();
    pt_source.change.emit();
""")

power_slider = Slider(start=0.1, end=4, value=1, step=.1, title="Power", callback=callback)
callback.args["power"] = power_slider

pt_slider = Slider(start=0, end=1, value=0.5, step=.1,
                     title="Point", callback=callback)
callback.args["pt"] = pt_slider

layout = column(power_slider, pt_slider, plot)

show(layout)

In [1]:
import numpy as np

from bokeh.io import output_notebook

from bokeh.layouts import row, column, widgetbox, Spacer, layout
from bokeh.models import CustomJS, ColumnDataSource, Slider, ColorBar, LinearColorMapper

from bokeh.plotting import figure, output_file, show, ColumnDataSource

output_notebook()

x = [x*0.005 for x in range(0, 200 + 1)]
y = [x1 - 0.5 for x1 in x]
pt_x = [0]
pt_y = [pt_x[0] - 0.5]

source = ColumnDataSource(data=dict(x=x, y=y))
pt_source = ColumnDataSource(data=dict(pt_x=pt_x, pt_y=pt_y))

plot = figure()
plot.line('x', 'y', source=source, line_width=3, line_alpha=0.6)

plot.circle('pt_x', 'pt_y', source=pt_source, size=20, color="red", alpha=0.5)

N = 500
x = np.linspace(0, 1, N)
y = np.linspace(0, 1, N)
xx, yy = np.meshgrid(x, y)
d = xx * yy * 0

x_min = 300
x_max = 400
y_min = 200
y_max = 300

d[x_min:x_max, y_min:y_max] = -0.5

p = figure(x_range=(0, 1), y_range=(0, 1),
           tooltips=[("x", "$x"), ("y", "$y"), ("value", "@image")])

color_mapper = LinearColorMapper(palette="Viridis256", low=-0.5, high=0.5)

im_source = ColumnDataSource(data=dict(image=[d]))

p.image(image='image', x=0, y=0, dw=1, dh=1, color_mapper=color_mapper, source=im_source)

color_bar = ColorBar(color_mapper=color_mapper, location=(0, 0))

p.add_layout(color_bar, 'right')

callback = CustomJS(args=dict(source=source, 
                              pt_source=pt_source, 
                              im_source=im_source,
                              x_min=300,
                              x_max=400,
                              y_min=200,
                              y_max=300), code="""
    var data = source.data;
    var pt_data = pt_source.data;
    var im_data = im_source.data;
    
    var image = im_data['image']
    
    var f = power.value;
    var x = data['x'];
    var y = data['y'];
    
    var pt_x = pt_data['pt_x']
    var pt_y = pt_data['pt_y']
    
    pt_x[0] = pt.value;
    pt_y[0] = Math.pow(pt_x[0], f) - 0.5;
    
    for (var i = 0; i < x.length; i++) {
        y[i] = Math.pow(x[i], f) - 0.5;
    }
    
    for (var i = 0; i < image.length; i++) {
        for (var j = 0; j < image[0].length; j++) {
            image[i][j] = pt_y[0];
        }
    }
    
    source.change.emit();
    pt_source.change.emit();
    im_source.change.emit();
""")

power_slider = Slider(start=0.1, end=4, value=1, step=.1, title="Power", callback=callback)
callback.args["power"] = power_slider

pt_slider = Slider(start=0, end=1, value=0, step=.1,
                     title="Point", callback=callback)
callback.args["pt"] = pt_slider

l = layout([widgetbox(power_slider, pt_slider), [plot, p]], sizing_mode='scale_width')

show(l)

Loading BokehJS ...

In [ ]:
d

In [ ]:
import numpy as np

from bokeh.layouts import row, widgetbox
from bokeh.models import CustomJS, Slider
from bokeh.plotting import figure, output_file, show, ColumnDataSource
from bokeh.io import output_notebook

x = np.linspace(0, 10, 500)
y = np.sin(x)

source = ColumnDataSource(data=dict(x=x, y=y))

plot = figure(y_range=(-10, 10), plot_width=400, plot_height=400)

plot.line('x', 'y', source=source, line_width=3, line_alpha=0.6)

callback = CustomJS(args=dict(source=source), code="""
    var data = source.data;
    var A = amp.value;
    var k = freq.value;
    var phi = phase.value;
    var B = offset.value;
    var x = data['x']
    var y = data['y']
    for (var i = 0; i < x.length; i++) {
        y[i] = B + A*Math.sin(k*x[i]+phi);
    }
    source.change.emit();
""")

amp_slider = Slider(start=0.1, end=10, value=1, step=.1,
                    title="Amplitude", callback=callback)
callback.args["amp"] = amp_slider

freq_slider = Slider(start=0.1, end=10, value=1, step=.1,
                     title="Frequency", callback=callback)
callback.args["freq"] = freq_slider

phase_slider = Slider(start=0, end=6.4, value=0, step=.1,
                      title="Phase", callback=callback)
callback.args["phase"] = phase_slider

offset_slider = Slider(start=-5, end=5, value=0, step=.1,
                       title="Offset", callback=callback)
callback.args["offset"] = offset_slider

layout = row(
    widgetbox(amp_slider, freq_slider, phase_slider, offset_slider),
    
    plot,
)

output_notebook()

show(layout)

In [7]:
type(source.data['x'])

list

In [5]:
import numpy as np

from bokeh.io import output_notebook

from bokeh.layouts import row, column, widgetbox, Spacer, layout
from bokeh.models import CustomJS, ColumnDataSource, Slider, ColorBar, LinearColorMapper

from bokeh.plotting import figure, output_file, show, ColumnDataSource


x = [x*0.005 for x in range(0, 200 + 1)]
y = [x1 - 0.5 for x1 in x]
pt_x = [0]
pt_y = [pt_x[0] - 0.5]

source = ColumnDataSource(data=dict(x=x, y=y))
pt_source = ColumnDataSource(data=dict(pt_x=pt_x, pt_y=pt_y))

plot = figure()
plot.line('x', 'y', source=source, line_width=3, line_alpha=0.6)

plot.circle('pt_x', 'pt_y', source=pt_source, size=20, color="red", alpha=0.5)

N = 500
x = np.linspace(0, 1, N)
y = np.linspace(0, 1, N)
xx, yy = np.meshgrid(x, y)
d = xx * yy * 0

x_min = 300
x_max = 400
y_min = 200
y_max = 300

d[x_min:x_max, y_min:y_max] = -0.5

p = figure(x_range=(0, 1), y_range=(0, 1),
           tooltips=[("x", "$x"), ("y", "$y"), ("value", "@image")])

color_mapper = LinearColorMapper(palette="Viridis256", low=-0.5, high=0.5)

im_source = ColumnDataSource(data=dict(image=[d]))

p.image('image', x=0, y=0, dw=1, dh=1, color_mapper=color_mapper, source=im_source)

color_bar = ColorBar(color_mapper=color_mapper, location=(0, 0))

p.add_layout(color_bar, 'right')

callback = CustomJS(args=dict(source=source, 
                              pt_source=pt_source, 
                              im_source=im_source,
                              x_min=300,
                              x_max=400,
                              y_min=200,
                              y_max=300,
                              N=500), code="""
    var data = source.data;
    var pt_data = pt_source.data;
    var im_data = im_source.data;
    
    var image = im_data['image'];
    
    var f = power.value;
    var x = data['x'];
    var y = data['y'];
    
    var pt_x = pt_data['pt_x']
    var pt_y = pt_data['pt_y']
    
    pt_x[0] = pt.value;
    pt_y[0] = Math.pow(pt_x[0], f) - 0.5;
    
    for (var i = 0; i < x.length; i++) {
        y[i] = Math.pow(x[i], f) - 0.5;
    }
    
    for (var i = x_min; i < x_max; i++) {
        for (var j = y_min; j < y_max; j++) {
            image[0][N * i + j] = pt_y[0];
        }
    }
    
    source.change.emit();
    pt_source.change.emit();
    im_source.change.emit();
""")

power_slider = Slider(start=0.1, end=4, value=1, step=.1, title="Power", callback=callback)
callback.args["power"] = power_slider

pt_slider = Slider(start=0, end=1, value=0, step=.01,
                     title="Point", callback=callback)
callback.args["pt"] = pt_slider

l = layout([widgetbox(power_slider, pt_slider), [plot, p]], sizing_mode='scale_width')

# output_file("slider.html", title="slider.py example")
output_notebook()

show(l)

Loading BokehJS ...